In [1]:
import csv
from osgeo import gdal
import fiona
import pandas as pd
import numpy as np
import geopandas as gpd
import shapely
from shapely import wkt
import matplotlib.pyplot as plt
from SPARQLWrapper import SPARQLWrapper, CSV
import folium
from folium.plugins import MarkerCluster

### Wildfire query

In [2]:
sparql = SPARQLWrapper("https://stko-kwg.geog.ucsb.edu/graphdb/repositories/KWG")
sparql.setReturnFormat(CSV)

fire_query = """PREFIX rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#>
PREFIX kwg-ont: <http://stko-kwg.geog.ucsb.edu/lod/ontology/>
PREFIX kwgr: <http://stko-kwg.geog.ucsb.edu/lod/resource/>
PREFIX time: <http://www.w3.org/2006/time#>
PREFIX geo: <http://www.opengis.net/ont/geosparql#>
select * where { 
    ?fire rdf:type kwg-ont:MTBSFire .
    ?fire kwg-ont:sfWithin kwgr:Earth.North_America.United_States.USA.5.42_1 .
    ?fire kwg-ont:hasTemporalScope ?temporal_scope .
    ?fire kwg-ont:hasFireName ?name .
    ?fire geo:hasGeometry ?geom .
    ?geom geo:asWKT ?wkt .
    ?temporal_scope time:inXSDgYear ?year .	
}"""
sparql.setQuery(fire_query)
try:
    res = sparql.query().convert()
    with open('fires.csv','wb') as file:
        file.write(res)
except Exception as e:
    print(f"There was a problem retrieving the fires: {e}")

### Road query

In [3]:
road_query = """PREFIX sf: <http://www.opengis.net/ont/sf#>
PREFIX kwgr: <http://stko-kwg.geog.ucsb.edu/lod/resource/>
PREFIX kwg-ont: <http://stko-kwg.geog.ucsb.edu/lod/ontology/>
PREFIX geo: <http://www.opengis.net/ont/geosparql#>
PREFIX geosparql: <http://www.opengis.net/ont/geosparql#>
PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>
PREFIX rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#>
select ?sign ?wkt where { 
    ?s rdf:type <http://stko-kwg.geog.ucsb.edu/lod/ontology/RoadSegment> .
    ?s rdfs:label ?road .
    ?s kwg-ont:hasRoadSign ?sign .
    ?s kwg-ont:sfWithin kwgr:Earth.North_America.United_States.USA.5.42_1 .
    ?s geo:hasGeometry ?geometry .
    ?geometry geosparql:asWKT ?wkt .
}"""
sparql.setQuery(road_query)
try:
    res = sparql.query().convert()
    with open('roads.csv','wb') as file:
        file.write(res)
except Exception as e:
    print(f"There was a problem retrieving the roads: {e}")

### Hospital query

In [4]:
hospital_query = """PREFIX kwg-ont: <http://stko-kwg.geog.ucsb.edu/lod/ontology/>
PREFIX kwgr: <http://stko-kwg.geog.ucsb.edu/lod/resource/>
PREFIX geosparql: <http://www.opengis.net/ont/geosparql#>
select ?hospital ?has_helipad ?name ?bed_count ?wkt where { 
    ?hospital a kwg-ont:Hospital .
    ?hospital kwg-ont:helipadAvailability ?has_helipad .
    ?hospital kwg-ont:hospitalName ?name .
    ?hospital kwg-ont:noHospitalBeds ?bed_count .
    ?hospital geosparql:hasDefaultGeometry ?geom .
    ?geom geosparql:asWKT ?wkt .
    kwgr:Earth.North_America.United_States.USA.5.42_1 kwg-ont:sfContains ?s2Cell.
    ?hospital kwg-ont:sfWithin ?s2Cell .
}"""
sparql.setQuery(hospital_query)
try:
    res = sparql.query().convert()
    with open('hospitals.csv','wb') as file:
            file.write(res)
except Exception as e:
    print(f"There was a problem retrieving the hospitals: {e}")

### Park query

In [5]:
park_query = """PREFIX gnis: <http://gnis-ld.org/lod/gnis/ontology/>
PREFIX rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#>
PREFIX usgs: <http://gnis-ld.org/lod/usgs/ontology/>
PREFIX kwg-ont: <http://stko-kwg.geog.ucsb.edu/lod/ontology/>
PREFIX kwgr: <http://stko-kwg.geog.ucsb.edu/lod/resource/>
PREFIX ago: <http://awesemantic-geo.link/ontology/>
PREFIX geosparql: <http://www.opengis.net/ont/geosparql#>
select * where { 
    ?park rdf:type usgs:Park .
    ?park kwg-ont:sfWithin kwgr:Earth.North_America.United_States.USA.5.42_1 .
    ?park gnis:officialName ?name .
    ?park ago:geometry ?geom .
    ?geom geosparql:asWKT ?wkt .
}"""
sparql.setQuery(park_query)
try:
    res = sparql.query().convert()
    with open('parks.csv','wb') as file:
            file.write(res)
except Exception as e:
    print(f"There was a problem retrieving the parks: {e}")

### School query

In [6]:
school_query = """PREFIX gnis: <http://gnis-ld.org/lod/gnis/ontology/>
PREFIX rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#>
PREFIX usgs: <http://gnis-ld.org/lod/usgs/ontology/>
PREFIX kwg-ont: <http://stko-kwg.geog.ucsb.edu/lod/ontology/>
PREFIX kwgr: <http://stko-kwg.geog.ucsb.edu/lod/resource/>
PREFIX ago: <http://awesemantic-geo.link/ontology/>
PREFIX geosparql: <http://www.opengis.net/ont/geosparql#>
select * where { 
    ?school rdf:type usgs:School .
    ?school kwg-ont:sfWithin kwgr:Earth.North_America.United_States.USA.5.42_1 .
    ?school gnis:officialName ?name .
    ?school ago:geometry ?geom .
    ?geom geosparql:asWKT ?wkt .
}"""
sparql.setQuery(school_query)
try:
    res = sparql.query().convert()
    with open('schools.csv','wb') as file:
            file.write(res)
except Exception as e:
    print(f"There was a problem retrieving the schools: {e}")

### Map Visualization

In [2]:
# load shapefile
santa_barbara_shape = gpd.read_file('shapefile/SB_County.shp')

# check coordinate reference system
santa_barbara_shape.crs

<Geographic 2D CRS: EPSG:4269>
Name: NAD83
Axis Info [ellipsoidal]:
- Lat[north]: Geodetic latitude (degree)
- Lon[east]: Geodetic longitude (degree)
Area of Use:
- name: North America - onshore and offshore: Canada - Alberta; British Columbia; Manitoba; New Brunswick; Newfoundland and Labrador; Northwest Territories; Nova Scotia; Nunavut; Ontario; Prince Edward Island; Quebec; Saskatchewan; Yukon. Puerto Rico. United States (USA) - Alabama; Alaska; Arizona; Arkansas; California; Colorado; Connecticut; Delaware; Florida; Georgia; Hawaii; Idaho; Illinois; Indiana; Iowa; Kansas; Kentucky; Louisiana; Maine; Maryland; Massachusetts; Michigan; Minnesota; Mississippi; Missouri; Montana; Nebraska; Nevada; New Hampshire; New Jersey; New Mexico; New York; North Carolina; North Dakota; Ohio; Oklahoma; Oregon; Pennsylvania; Rhode Island; South Carolina; South Dakota; Tennessee; Texas; Utah; Vermont; Virginia; Washington; West Virginia; Wisconsin; Wyoming. US Virgin Islands. British Virgin Islands

In [3]:
# convert csv files to geodataframe
def convert_gdf(input_file):
    df = pd.read_csv(input_file)
    if "<" in df['wkt'][0]:
        for _, r in df.iterrows():
            r['wkt'] = r['wkt'].split('>')[1]
    df['wkt'] = df['wkt'].apply(wkt.loads)
    output_gdf = gpd.GeoDataFrame(df,geometry=df['wkt'], crs='epsg:4326')
    output_gdf = output_gdf.to_crs(santa_barbara_shape.crs)
    return output_gdf

In [4]:
line_data = convert_gdf('roads.csv')
hospital_data = convert_gdf('hospitals.csv')
fire_data = convert_gdf('fires.csv')
park_data = convert_gdf('parks.csv')
school_data = convert_gdf('schools.csv')

In [5]:
# create an initial centroid coordinate for map
init_x = (min(santa_barbara_shape.bounds['minx']) + max(santa_barbara_shape.bounds['maxx']))/2
init_y = (min(santa_barbara_shape.bounds['miny']) + max(santa_barbara_shape.bounds['maxy']))/2

sb_map = folium.Map(location=[init_y, init_x], zoom_start=8)
folium.GeoJson(data=santa_barbara_shape, name='Santa Barbara County').add_to(sb_map)
sb_map

In [6]:
# add roads
feature_group_road = folium.FeatureGroup("Roads")
for _, r in line_data.iterrows():
    line_string = gpd.GeoSeries(r['geometry']).simplify(tolerance=0.001)
    road = line_string.to_json()
    road = folium.GeoJson(data=road,style_function=lambda x: {'color': 'red','weight': 3})
    feature_group_road.add_child(road)

# add hospitals
feature_group_hospital = folium.FeatureGroup("Hospitals")
for _, r in hospital_data.iterrows():
    popup = folium.Popup(str(r['name'])+'<br>'+'Bed Count: '+ str(r['bed_count']), max_width=300)
    feature_group_hospital.add_child(folium.Marker(location=[r['wkt'].y, r['wkt'].x], 
                                                   icon=folium.Icon(color='red',icon='medkit', prefix="fa"), popup=popup))
    
# add schools as cluster
marker_cluster_school = MarkerCluster(name="Schools")
for _, r in school_data.iterrows():
    popup = folium.Popup(r['name'], max_width=200)
    marker_cluster_school.add_child(folium.Marker(location=[r['wkt'].y, r['wkt'].x], 
                                                  icon=folium.Icon(color="blue",icon='graduation-cap',prefix="fa"), 
                                                  popup=popup))

# add parks as cluster
marker_cluster_park = MarkerCluster(name = "Parks")
for _, r in park_data.iterrows():
    popup = folium.Popup(r['name'], max_width=200)
    marker_cluster_park.add_child(folium.Marker(location=[r['wkt'].y, r['wkt'].x], 
                                                icon=folium.Icon(color="green",icon='tree',prefix='fa'), 
                                                popup=popup))
    
# add wildfire polygons
feature_group_fire = folium.FeatureGroup("Fires")
for _, r in fire_data.iterrows():
    fire_polygons = gpd.GeoSeries(r['geometry']).simplify(tolerance=0.001)
    fire = fire_polygons.to_json()
    fire = folium.GeoJson(data=fire,style_function=lambda x: {'fillColor': 'orange','color': 'orange','weight': 1})
    popup = folium.Popup(str(r['name'])+" FIRE, "+str(r['year']), max_width=200)
    popup.add_to(fire)
    feature_group_fire.add_child(fire)

sb_map.add_child(feature_group_road)
sb_map.add_child(feature_group_hospital)
sb_map.add_child(feature_group_fire)
sb_map.add_child(marker_cluster_school)
sb_map.add_child(marker_cluster_park)

# try different base map layers
folium.TileLayer('Cartodb Positron').add_to(sb_map)
folium.TileLayer('Stamen Toner').add_to(sb_map)

# add layer control
folium.LayerControl().add_to(sb_map)
sb_map